In [1]:
#!/usr/bin/env python3

"""
Demonstrates how to:
    * use the MAML wrapper for fast-adaptation,
    * use the benchmark interface to load mini-ImageNet, and
    * sample tasks and split them in adaptation and evaluation sets.

To contrast the use of the benchmark interface with directly instantiating mini-ImageNet datasets and tasks, compare with `protonet_miniimagenet.py`.
"""

import random
import numpy as np
import torch
from torch import nn, optim
import matplotlib.pyplot as plt
import learn2learn as l2l
from learn2learn.data.transforms import (NWays,
                                         KShots,
                                         LoadData,
                                         RemapLabels,
                                         ConsecutiveLabels)
import os

In [ ]:


def accuracy(predictions, targets):
    predictions = predictions.argmax(dim=1).view(targets.shape)
    return (predictions == targets).sum().float() / targets.size(0)


def fast_adapt(batch, learner, loss, adaptation_steps, shots, ways, device):
    data, labels = batch
    data, labels = data.to(device), labels.to(device)

    # Separate data into adaptation/evalutation sets
    adaptation_indices = np.zeros(data.size(0), dtype=bool)
    adaptation_indices[np.arange(shots*ways) * 2] = True
    evaluation_indices = torch.from_numpy(~adaptation_indices)
    adaptation_indices = torch.from_numpy(adaptation_indices)
    adaptation_data, adaptation_labels = data[adaptation_indices], labels[adaptation_indices]
    evaluation_data, evaluation_labels = data[evaluation_indices], labels[evaluation_indices]

    # Adapt the model
    for step in range(adaptation_steps):
        adaptation_error = loss(learner(adaptation_data), adaptation_labels)
        learner.adapt(adaptation_error)

    # Evaluate the adapted model
    predictions = learner(evaluation_data)
    evaluation_error = loss(predictions, evaluation_labels)
    evaluation_accuracy = accuracy(predictions, evaluation_labels)
    return evaluation_error, evaluation_accuracy


def perform_experiment(dataset,
        ways=5,
        shots=5,
        meta_lr=0.003,
        fast_lr=0.5,
        meta_batch_size=32,
        adaptation_steps=1,
        num_iterations=60000,
        cuda=True,
        seed=42,
):
    
    Meta_Train_Accuracy = []
    Meta_Train_Error = []
    Meta_Val_Accuracy = []
    Meta_Val_Error = []
#     Iterations = []
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    device = torch.device('cpu')
    if cuda and torch.cuda.device_count():
        torch.cuda.manual_seed(seed)
        device = torch.device('cuda')

    # Create Tasksets using the benchmark interface
    tasksets = l2l.vision.benchmarks.get_tasksets(dataset,
                                                  train_samples=2*shots,
                                                  train_ways=ways,
                                                  test_samples=2*shots,
                                                  test_ways=ways,
                                                  root='~/data',
    )

    # Create model
    model = l2l.vision.models.MiniImagenetCNN(ways)
    model.to(device)
    maml = l2l.algorithms.MAML(model, lr=fast_lr, first_order=False)
    opt = optim.Adam(maml.parameters(), meta_lr)
    loss = nn.CrossEntropyLoss(reduction='mean')

    for iteration in range(num_iterations):
        opt.zero_grad()
        meta_train_error = 0.0
        meta_train_accuracy = 0.0
        meta_valid_error = 0.0
        meta_valid_accuracy = 0.0
        for task in range(meta_batch_size):
            # Compute meta-training loss
            learner = maml.clone()
            batch = tasksets.train.sample()
            evaluation_error, evaluation_accuracy = fast_adapt(batch,
                                                               learner,
                                                               loss,
                                                               adaptation_steps,
                                                               shots,
                                                               ways,
                                                               device)
            evaluation_error.backward()
            meta_train_error += evaluation_error.item()
            meta_train_accuracy += evaluation_accuracy.item()

            # Compute meta-validation loss
            learner = maml.clone()
            batch = tasksets.validation.sample()
            evaluation_error, evaluation_accuracy = fast_adapt(batch,
                                                               learner,
                                                               loss,
                                                               adaptation_steps,
                                                               shots,
                                                               ways,
                                                               device)
            meta_valid_error += evaluation_error.item()
            meta_valid_accuracy += evaluation_accuracy.item()

        # Print some metrics
#         print('\n')
#         print('Iteration', iteration)
#         print('Meta Train Error', meta_train_error / meta_batch_size)
#         print('Meta Train Accuracy', meta_train_accuracy / meta_batch_size)
#         print('Meta Valid Error', meta_valid_error / meta_batch_size)
#         print('Meta Valid Accuracy', meta_valid_accuracy / meta_batch_size)
        
        meta_train_error =  meta_train_error / meta_batch_size
        meta_train_accuracy = meta_train_accuracy / meta_batch_size
        meta_val_error =  meta_valid_error / meta_batch_size
        meta_val_accuracy = meta_valid_accuracy / meta_batch_size
        if(iteration % 4 ==0):
            print('\n')
            print('Iteration', iteration)
            print('Meta Train Error', meta_train_error)
            print('Meta Train Accuracy', meta_train_accuracy)
            print('Meta Valid Error', meta_val_error)
            print('Meta Valid Accuracy', meta_val_accuracy)

        Meta_Train_Accuracy.append(meta_train_accuracy)
        Meta_Train_Error.append(meta_train_error)
        Meta_Val_Accuracy.append(meta_val_accuracy)
        Meta_Val_Error.append(meta_val_error)

        # Average the accumulated gradients and optimize
        for p in maml.parameters():
            p.grad.data.mul_(1.0 / meta_batch_size)
        opt.step()

    meta_test_error = 0.0
    meta_test_accuracy = 0.0
    for task in range(meta_batch_size):
        # Compute meta-testing loss
        learner = maml.clone()
        batch = tasksets.test.sample()
        evaluation_error, evaluation_accuracy = fast_adapt(batch,
                                                           learner,
                                                           loss,
                                                           adaptation_steps,
                                                           shots,
                                                           ways,
                                                           device)
        meta_test_error += evaluation_error.item()
        meta_test_accuracy += evaluation_accuracy.item()
#     print('Meta Test Error', meta_test_error / meta_batch_size)
#     print('Meta Test Accuracy', meta_test_accuracy / meta_batch_size)
    Meta_Test_Error = meta_test_error / meta_batch_size
    print('Meta Test Error', Meta_Test_Error)
    Meta_Test_Accuracy = meta_test_accuracy / meta_batch_size
    print('Meta Test Accuracy', Meta_Test_Accuracy)
    
    if not os.path.exists('plots'):
        os.makedirs('plots')
    if not os.path.exists('plots/acc'):
        os.makedirs('plots/acc')
    if not os.path.exists('plots/loss'):
        os.makedirs('plots/loss')
        
    ###### Plot Accuracies ######
    props = dict(boxstyle='round', facecolor='wheat', alpha=0.5)
    fig = plt.figure()
    ax = plt.subplot(111)
    ax.plot(list(range(0, len(Meta_Train_Accuracy))), Meta_Train_Accuracy, label="Meta Train ")
    ax.plot(list(range(0, len(Meta_Val_Accuracy))), Meta_Val_Accuracy, label="Meta Val")
#     ax.text((len(Meta_Val_Accuracy)/2), 0, 'Meta Test:{0}'.format(round(meta_test_accuracy, 2)), style='italic',
#         bbox={'facecolor': 'red', 'alpha': 0.25, 'pad': 5})
    # place a text box in upper left in axes coords
    ax.text(0.05, 0.5, 'Meta Test:{0}'.format(round(Meta_Test_Accuracy, 2)), transform=ax.transAxes, fontsize=14,
            verticalalignment='top', bbox=props)
    plt.title('Adaption')
    plt.xlabel('Iteration')
    plt.ylabel('Meta Accuracy')
    ax.legend()
    plt.savefig('./plots/acc/{0}_ways_{1}_shots_{2}_Acc_I_{3}.png'.format(dataset, ways, shots, num_iterations),
               dpi=150)
    ###### Plot Accuracies ######

    ###### Plot Errors ######
    fig = plt.figure()
    ax = plt.subplot(111)
    ax.plot(list(range(0, len(Meta_Train_Error))), Meta_Train_Error, label="Meta Train ")
    ax.plot(list(range(0, len(Meta_Val_Error))), Meta_Val_Accuracy, label="Meta Val Lss")
#     ax.text((len(Meta_Val_Accuracy)/2),0, 'Meta Test Accuracy:{0}  Meta Test Loss:{1}'.format(round(meta_test_accuracy, 2),
#                               round(meta_test_error, 2)), style='italic',
#         bbox={'facecolor': 'red', 'alpha': 0.25, 'pad': 5})
    ax.text(0.05, 0.5, 'MTestAcc:{0}  MTestLoss:{1}'.format(round(Meta_Test_Accuracy, 2),
                                           round(Meta_Test_Error, 2)), transform=ax.transAxes, fontsize=14,
            verticalalignment='top', bbox=props)
    plt.title('Adaption')
    plt.xlabel('Iteration')
    plt.ylabel('Meta Loss')
    ax.legend()
    plt.savefig('./plots/loss/{0}_ways_{1}_shots_{2}_Loss_I_{3}.png'.format(dataset, ways, shots, num_iterations), dpi=150)
    ###### Plot Errors ######


if __name__ == '__main__':
    Ways = [5]
    Shots = [1, 5]
    Iterations = [4, 10000, 60000, 120000]
    for ways in Ways:
        for shots in Shots:
            for iteration in Iterations:
                
                perform_experiment(dataset='mini-imagenet',
                ways=ways,
                shots=shots,
                meta_lr=0.003,
                fast_lr=0.5,
                meta_batch_size=32,
                adaptation_steps=1,
                num_iterations=iteration,
                cuda=True,
                seed=42)



Iteration 0
Meta Train Error 9.065270334482193
Meta Train Accuracy 0.18750000279396772
Meta Valid Error 8.114383235573769
Meta Valid Accuracy 0.218750003259629
Meta Test Error 2.9810838401317596
Meta Test Accuracy 0.2500000041909516


Iteration 0
Meta Train Error 9.065270349383354
Meta Train Accuracy 0.18750000279396772
Meta Valid Error 8.114383205771446
Meta Valid Accuracy 0.218750003259629


Iteration 4
Meta Train Error 3.1605596393346786
Meta Train Accuracy 0.20625000353902578
Meta Valid Error 3.3016852512955666
Meta Valid Accuracy 0.21250000316649675


Iteration 8
Meta Train Error 2.9107124265283346
Meta Train Accuracy 0.2312500048428774
Meta Valid Error 2.9324699081480503
Meta Valid Accuracy 0.18750000279396772


Iteration 12
Meta Train Error 2.6482501924037933
Meta Train Accuracy 0.26250000577419996
Meta Valid Error 2.5280242413282394
Meta Valid Accuracy 0.2687500067986548


Iteration 16
Meta Train Error 2.49200801178813
Meta Train Accuracy 0.22500000428408384
Meta Valid Error 



Iteration 192
Meta Train Error 1.6412769705057144
Meta Train Accuracy 0.26875000493600965
Meta Valid Error 1.5559979639947414
Meta Valid Accuracy 0.35000000754371285


Iteration 196
Meta Train Error 1.5383914783596992
Meta Train Accuracy 0.3000000067986548
Meta Valid Error 1.5699795223772526
Meta Valid Accuracy 0.29375000623986125


Iteration 200
Meta Train Error 1.5199007224291563
Meta Train Accuracy 0.3437500069849193
Meta Valid Error 1.5664385966956615
Meta Valid Accuracy 0.32500000623986125


Iteration 204
Meta Train Error 1.5504964962601662
Meta Train Accuracy 0.30625000642612576
Meta Valid Error 1.4989206083118916
Meta Valid Accuracy 0.3812500098720193


Iteration 208
Meta Train Error 1.5371218547224998
Meta Train Accuracy 0.3312500058673322
Meta Valid Error 1.5633290857076645
Meta Valid Accuracy 0.287500006146729


Iteration 212
Meta Train Error 1.5173266790807247
Meta Train Accuracy 0.3062500059604645
Meta Valid Error 1.6000012420117855
Meta Valid Accuracy 0.2187500037252903




Iteration 392
Meta Train Error 1.5389835052192211
Meta Train Accuracy 0.35000000707805157
Meta Valid Error 1.4902500286698341
Meta Valid Accuracy 0.3187500066123903


Iteration 396
Meta Train Error 1.5423346143215895
Meta Train Accuracy 0.28125000512227416
Meta Valid Error 1.5637528263032436
Meta Valid Accuracy 0.25000000605359674


Iteration 400
Meta Train Error 1.5586075223982334
Meta Train Accuracy 0.318750006146729
Meta Valid Error 1.5177394822239876
Meta Valid Accuracy 0.32500000670552254


Iteration 404
Meta Train Error 1.4645848795771599
Meta Train Accuracy 0.32500000670552254
Meta Valid Error 1.624443881213665
Meta Valid Accuracy 0.30000000540167093


Iteration 408
Meta Train Error 1.3808814361691475
Meta Train Accuracy 0.4187500113621354
Meta Valid Error 1.5921297781169415
Meta Valid Accuracy 0.2875000052154064


Iteration 412
Meta Train Error 1.425509762018919
Meta Train Accuracy 0.37500000838190317
Meta Valid Error 1.4596694819629192
Meta Valid Accuracy 0.36250000912696123



Iteration 592
Meta Train Error 1.4750675689429045
Meta Train Accuracy 0.3875000081025064
Meta Valid Error 1.5011012814939022
Meta Valid Accuracy 0.36250000866129994


Iteration 596
Meta Train Error 1.4746219366788864
Meta Train Accuracy 0.3250000081025064
Meta Valid Error 1.5407486204057932
Meta Valid Accuracy 0.3250000076368451


Iteration 600
Meta Train Error 1.4494916833937168
Meta Train Accuracy 0.3687500092200935
Meta Valid Error 1.5716561488807201
Meta Valid Accuracy 0.3437500079162419


Iteration 604
Meta Train Error 1.4610552489757538
Meta Train Accuracy 0.37500000931322575
Meta Valid Error 1.537537693977356
Meta Valid Accuracy 0.3125000074505806


Iteration 608
Meta Train Error 1.4554184954613447
Meta Train Accuracy 0.3687500092200935
Meta Valid Error 1.5710935816168785
Meta Valid Accuracy 0.31875000754371285


Iteration 612
Meta Train Error 1.464755605906248
Meta Train Accuracy 0.3750000079162419
Meta Valid Error 1.6108430735766888
Meta Valid Accuracy 0.29375000670552254






Iteration 792
Meta Train Error 1.3994815554469824
Meta Train Accuracy 0.3937500100582838
Meta Valid Error 1.4873052053153515
Meta Valid Accuracy 0.3437500074505806


Iteration 796
Meta Train Error 1.396957866847515
Meta Train Accuracy 0.40000001015141606
Meta Valid Error 1.5392160154879093
Meta Valid Accuracy 0.29375000623986125


Iteration 800
Meta Train Error 1.480103425681591
Meta Train Accuracy 0.4000000092200935
Meta Valid Error 1.477636868134141
Meta Valid Accuracy 0.318750006146729


Iteration 804
Meta Train Error 1.4471142571419477
Meta Train Accuracy 0.40000001015141606
Meta Valid Error 1.533658929169178
Meta Valid Accuracy 0.33125000912696123


Iteration 808
Meta Train Error 1.333843057975173
Meta Train Accuracy 0.44375001080334187
Meta Valid Error 1.4583570286631584
Meta Valid Accuracy 0.3562500081025064


Iteration 812
Meta Train Error 1.3479119930416346
Meta Train Accuracy 0.44375001080334187
Meta Valid Error 1.438358098268509
Meta Valid Accuracy 0.3625000100582838


Ite

...



Iteration 9912
Meta Train Error 1.067513758316636
Meta Train Accuracy 0.5562500115483999
Meta Valid Error 1.361385865136981
Meta Valid Accuracy 0.4250000100582838


Iteration 9916
Meta Train Error 1.0773219168186188
Meta Train Accuracy 0.5625000107102096
Meta Valid Error 1.2308710413053632
Meta Valid Accuracy 0.543750012293458


Iteration 9920
Meta Train Error 1.252561142668128
Meta Train Accuracy 0.5375000131316483
Meta Valid Error 1.367587674409151
Meta Valid Accuracy 0.41875001043081284


Iteration 9924
Meta Train Error 1.1359897870570421
Meta Train Accuracy 0.5500000123865902
Meta Valid Error 1.3057757318019867
Meta Valid Accuracy 0.4562500100582838


Iteration 9928
Meta Train Error 1.1040840363129973
Meta Train Accuracy 0.5750000132247806
Meta Valid Error 1.3344255341216922
Meta Valid Accuracy 0.43125001061707735


Iteration 9932
Meta Train Error 1.008802249096334
Meta Train Accuracy 0.6062500146217644
Meta Valid Error 1.3004007581621408
Meta Valid Accuracy 0.4687500111758709






Iteration 10112
Meta Train Error 1.072555738966912
Meta Train Accuracy 0.5687500089406967
Meta Valid Error 1.2314218915998936
Meta Valid Accuracy 0.4875000105239451


Iteration 10116
Meta Train Error 1.0538396006450057
Meta Train Accuracy 0.5875000115483999
Meta Valid Error 1.3032836159691215
Meta Valid Accuracy 0.4937500120140612


Iteration 10120
Meta Train Error 1.1110875075682998
Meta Train Accuracy 0.5687500135973096
Meta Valid Error 1.387587707489729
Meta Valid Accuracy 0.4250000100582838


Iteration 10124
Meta Train Error 1.0325462613254786
Meta Train Accuracy 0.518750011920929
Meta Valid Error 1.3334302604198456
Meta Valid Accuracy 0.4312500115483999


Iteration 10128
Meta Train Error 0.9892634665593505
Meta Train Accuracy 0.6062500146217644
Meta Valid Error 1.373321397230029
Meta Valid Accuracy 0.43750000977888703


Iteration 10132
Meta Train Error 1.117355527356267
Meta Train Accuracy 0.5437500136904418
Meta Valid Error 1.3587180078029633
Meta Valid Accuracy 0.4125000103376



Iteration 10308
Meta Train Error 1.0076073165982962
Meta Train Accuracy 0.606250012293458
Meta Valid Error 1.3071542475372553
Meta Valid Accuracy 0.46250001061707735


Iteration 10312
Meta Train Error 1.063031416386366
Meta Train Accuracy 0.6312500089406967
Meta Valid Error 1.3451905865222216
Meta Valid Accuracy 0.450000009033829


Iteration 10316
Meta Train Error 1.0370192639529705
Meta Train Accuracy 0.5937500135041773
Meta Valid Error 1.29097555950284
Meta Valid Accuracy 0.4625000078231096


Iteration 10320
Meta Train Error 1.0207097386009991
Meta Train Accuracy 0.5875000129453838
Meta Valid Error 1.4174158442765474
Meta Valid Accuracy 0.4000000096857548


Iteration 10324
Meta Train Error 1.1099449377506971
Meta Train Accuracy 0.5625000144354999
Meta Valid Error 1.2828117311000824
Meta Valid Accuracy 0.4687500102445483


Iteration 10328
Meta Train Error 1.117162705399096
Meta Train Accuracy 0.5375000108033419
Meta Valid Error 1.317332535982132
Meta Valid Accuracy 0.456250010989606



Iteration 10504
Meta Train Error 1.157711367122829
Meta Train Accuracy 0.5500000133179128
Meta Valid Error 1.249739432707429
Meta Valid Accuracy 0.4375000116415322


Iteration 10508
Meta Train Error 1.0964896962977946
Meta Train Accuracy 0.5750000113621354
Meta Valid Error 1.2331968042999506
Meta Valid Accuracy 0.5375000131316483


Iteration 10512
Meta Train Error 0.9461141359061003
Meta Train Accuracy 0.625000013038516
Meta Valid Error 1.339968042448163
Meta Valid Accuracy 0.41250000847503543


Iteration 10516
Meta Train Error 1.1287031173706055
Meta Train Accuracy 0.5937500102445483
Meta Valid Error 1.2594984769821167
Meta Valid Accuracy 0.4937500124797225


Iteration 10520
Meta Train Error 1.058583184145391
Meta Train Accuracy 0.5687500135973096
Meta Valid Error 1.2613809891045094
Meta Valid Accuracy 0.5000000139698386


Iteration 10524
Meta Train Error 0.9889099206775427
Meta Train Accuracy 0.5875000129453838
Meta Valid Error 1.3654256500303745
Meta Valid Accuracy 0.4625000129453



Iteration 10700
Meta Train Error 1.101554961875081
Meta Train Accuracy 0.5312500135041773
Meta Valid Error 1.2767464946955442
Meta Valid Accuracy 0.47500000847503543


Iteration 10704
Meta Train Error 1.0183966467157006
Meta Train Accuracy 0.562500013038516
Meta Valid Error 1.3274683374911547
Meta Valid Accuracy 0.42500000819563866


Iteration 10708
Meta Train Error 1.0110922800377011
Meta Train Accuracy 0.6000000145286322
Meta Valid Error 1.3827440831810236
Meta Valid Accuracy 0.4250000072643161


Iteration 10712
Meta Train Error 1.132185135036707
Meta Train Accuracy 0.5437500108964741
Meta Valid Error 1.3592379987239838
Meta Valid Accuracy 0.4250000100582838


Iteration 10716
Meta Train Error 0.9894798677414656
Meta Train Accuracy 0.6187500134110451
Meta Valid Error 1.2032239492982626
Meta Valid Accuracy 0.46250001108273864


Iteration 10720
Meta Train Error 0.985617620870471
Meta Train Accuracy 0.6125000133179128
Meta Valid Error 1.423682864755392
Meta Valid Accuracy 0.40000000968